In [28]:
!pip install scikit-learn
!pip install shap
!pip install umap
!pip install umap-learn
!pip install pyarrow
!pip install matplotlib
!pip install plotly
!pip install nbformat

In [29]:
import polars as pl
import gzip
from sklearn.cluster import DBSCAN, AgglomerativeClustering
from sklearn.ensemble import  RandomForestClassifier
from sklearn.impute import SimpleImputer
import numpy as np
from umap import UMAP
from matplotlib import pyplot as plt
import plotly
import plotly.graph_objects as go

In [30]:
df = pl.read_csv('~/buckets/b1/datasets/competencia_02_targets_b2.csv.gz', infer_schema_length=100000, dtypes={'foto_mes':str})

In [31]:
df.filter(pl.col("numero_de_cliente") == 29199686)

shape: (12, 155)
┌───────────┬──────────┬───────────┬───────────┬───┬───────────┬───────────┬───────────┬───────────┐
│ numero_de ┆ foto_mes ┆ active_qu ┆ cliente_v ┆ … ┆ Visa_ccon ┆ Visa_cade ┆ Visa_mpag ┆ clase_ter │
│ _cliente  ┆ ---      ┆ arter     ┆ ip        ┆   ┆ sumos     ┆ lantosefe ┆ ominimo   ┆ naria     │
│ ---       ┆ str      ┆ ---       ┆ ---       ┆   ┆ ---       ┆ ctivo     ┆ ---       ┆ ---       │
│ i64       ┆          ┆ i64       ┆ i64       ┆   ┆ i64       ┆ ---       ┆ f64       ┆ str       │
│           ┆          ┆           ┆           ┆   ┆           ┆ i64       ┆           ┆           │
╞═══════════╪══════════╪═══════════╪═══════════╪═══╪═══════════╪═══════════╪═══════════╪═══════════╡
│ 29199686  ┆ 201901   ┆ 1         ┆ 0         ┆ … ┆ 8         ┆ 0         ┆ 281.52    ┆ CONTINUA  │
│ 29199686  ┆ 201902   ┆ 1         ┆ 0         ┆ … ┆ 4         ┆ 0         ┆ 175.95    ┆ CONTINUA  │
│ 29199686  ┆ 201903   ┆ 1         ┆ 0         ┆ … ┆ 7         ┆ 0         ┆ 457.47    ┆ CONTINUA  │
│ 29199686  ┆ 201904   ┆ 1         ┆ 0         ┆ … ┆ 8         ┆ 0         ┆ 281.52    ┆ CONTINUA  │
│ …         ┆ …        ┆ …         ┆ …         ┆ … ┆ …         ┆ …         ┆ …         ┆ …         │
│ 29199686  ┆ 201909   ┆ 1         ┆ 0         ┆ … ┆ 4         ┆ 0         ┆ 211.14    ┆ CONTINUA  │
│ 29199686  ┆ 201910   ┆ 1         ┆ 0         ┆ … ┆ 8         ┆ 0         ┆ 398.82    ┆ CONTINUA  │
│ 29199686  ┆ 201911   ┆ 1         ┆ 0         ┆ … ┆ 4         ┆ 0         ┆ 363.63    ┆ BAJA+2    │
│ 29199686  ┆ 201912   ┆ 1         ┆ 0         ┆ … ┆ 3         ┆ 0         ┆ 551.31    ┆ BAJA+1    │
└───────────┴──────────┴───────────┴───────────┴───┴───────────┴───────────┴───────────┴───────────┘

In [32]:
df.unique(subset=["numero_de_cliente"]).shape

(18967, 155)

In [33]:
max_lag = 12
columns = df.columns 
columns.remove('foto_mes')
columns.remove('numero_de_cliente')
columns.remove('clase_ternaria')

for column in columns:
    for lag in range(1, max_lag+1):    
        column_lag = column + '_lag_' + str(lag)
        df = df.with_columns([pl.col(column).shift(lag).over('numero_de_cliente').alias(column_lag)])

In [34]:
df = df.filter(pl.col("clase_ternaria").is_in(['CONTINUA', 'BAJA+2']))
df2 = df.filter(
    (
        pl.col('clase_ternaria').ne('CONTINUA') | 
        (pl.col('clase_ternaria').eq('CONTINUA') & pl.lit(np.random.rand(df.height)).lt(0.1))
    )
)
df2 = df2.filter(pl.lit(np.random.rand(df2.height)).lt(0.5))
del df 
df = df2

In [35]:
df2.group_by('clase_ternaria').agg(pl.count('clase_ternaria').alias('count'))

shape: (2, 2)
┌────────────────┬───────┐
│ clase_ternaria ┆ count │
│ ---            ┆ ---   │
│ str            ┆ u32   │
╞════════════════╪═══════╡
│ BAJA+2         ┆ 9611  │
│ CONTINUA       ┆ 12494 │
└────────────────┴───────┘

In [36]:
list([c for c in df.columns if not 'lag' in c])

['numero_de_cliente',
 'foto_mes',
 'active_quarter',
 'cliente_vip',
 'internet',
 'cliente_edad',
 'cliente_antiguedad',
 'mrentabilidad',
 'mrentabilidad_annual',
 'mcomisiones',
 'mactivos_margen',
 'mpasivos_margen',
 'cproductos',
 'tcuentas',
 'ccuenta_corriente',
 'mcuenta_corriente_adicional',
 'mcuenta_corriente',
 'ccaja_ahorro',
 'mcaja_ahorro',
 'mcaja_ahorro_adicional',
 'mcaja_ahorro_dolares',
 'cdescubierto_preacordado',
 'mcuentas_saldo',
 'ctarjeta_debito',
 'ctarjeta_debito_transacciones',
 'mautoservicio',
 'ctarjeta_visa',
 'ctarjeta_visa_transacciones',
 'mtarjeta_visa_consumo',
 'ctarjeta_master',
 'ctarjeta_master_transacciones',
 'mtarjeta_master_consumo',
 'cprestamos_personales',
 'mprestamos_personales',
 'cprestamos_prendarios',
 'mprestamos_prendarios',
 'cprestamos_hipotecarios',
 'mprestamos_hipotecarios',
 'cplazo_fijo',
 'mplazo_fijo_dolares',
 'mplazo_fijo_pesos',
 'cinversion1',
 'minversion1_pesos',
 'minversion1_dolares',
 'cinversion2',
 'minversi

In [37]:
df.shape

(22105, 1979)

In [38]:
df_solo_baja = df.filter(pl.col('clase_ternaria') == 'BAJA+2')

In [39]:
df_solo_baja.shape
# df = df_solo_baja

(9611, 1979)

In [40]:
def distanceMatrix(model, X):

    terminals = model.apply(X)
    nTrees = terminals.shape[1]

    a = terminals[:,0]
    proxMat = 1*np.equal.outer(a, a)

    for i in range(1, nTrees):
        a = terminals[:,i]
        proxMat += 1*np.equal.outer(a, a)

    proxMat = proxMat / nTrees

    return proxMat.max() - proxMat


imp_mean = SimpleImputer(missing_values=np.nan, strategy='median')

XRF = df.drop(['clase_ternaria'])
YRF = df['clase_ternaria']

XRF_imp = imp_mean.fit_transform(XRF)

model = RandomForestClassifier(n_estimators=30, max_features=20, min_samples_leaf=400, )
model.fit(XRF_imp, YRF)
d = distanceMatrix(model, XRF_imp)

In [41]:
YRF = YRF.to_pandas()
embedding_rf = UMAP(
  n_components=3,
  n_neighbors=50,
  metric="precomputed",
).fit_transform(d[(YRF=="BAJA+2").index,][:,YRF=="BAJA+2"])


/home/marialejandramantillab/anaconda3/envs/dmef/lib/python3.11/site-packages/umap/umap_.py:1857: UserWarning: using precomputed metric; inverse_transform will be unavailable
  warn("using precomputed metric; inverse_transform will be unavailable")


In [47]:
plotly.offline.init_notebook_mode()
trace = go.Scatter3d(
    x=embedding_rf[:,0],
    y=embedding_rf[:,1],
    z=embedding_rf[:,2],
    mode='markers',
    marker=dict(
        size=2,
        opacity=0.8        
    )
)
# Configure the layout.
layout = go.Layout(
    margin={'l': 0, 'r': 0, 'b': 0, 't': 0}
)

data = [trace]

plot_figure = go.Figure(data=data, layout=layout)

# Render the plot.
plotly.offline.iplot(plot_figure)

clase_ternaria
CONTINUA    12494
BAJA+2       9611
Name: count, dtype: int64